In [12]:
import numpy as np
import csv
import os
import math
from sklearn.linear_model import LinearRegression

In [13]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [14]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [15]:
def GetFreq(AnnotData):
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      return AnnotData[cell_id][1].frame-AnnotData[cell_id][0].frame 
  return 1

In [16]:
def CalculateMovements(AnnotData, Robustness, Frequency, ComputerStartingFrame=0, ComputerEndingFrame=-1):
  SumMovements = 0
  SumDistances = 0
  NumElements = 0
  CellMovements = []

  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      prevx = AnnotData[cell_id][0].posx
      prevy = AnnotData[cell_id][0].posy
      StartFrame = AnnotData[cell_id][1].frame
      MaxDist = 0
      CurrentMovement = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if element.frame>=ComputerStartingFrame and (ComputerEndingFrame==-1 or element.frame<=ComputerEndingFrame):
          if np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
            CurrentMovement += np.sqrt(np.power(element.posx-prevx,2)+np.power(element.posy-prevy,2))
            NumElements += 1
            prevx = element.posx
            prevy = element.posy
            DistFromZeroPos = np.sqrt(np.power(element.posx-AnnotData[cell_id][0].posx,2)+np.power(element.posy-AnnotData[cell_id][0].posy,2))
            if DistFromZeroPos>MaxDist:
              MaxDist = DistFromZeroPos
          counter+=1
      SumDistances += MaxDist
      CellMovements.append(CurrentMovement)

  #Applying robust mean
  CellMovements.sort()
  if Robustness != 0:
    NumData = len(CellMovements)
    CellMovements = CellMovements[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumMovements = sum(CellMovements)

  if NumElements!=0:
    SumMovements /= NumElements
    SumDistances /= NumElements
  else:
    SumMovements = 0
    SumDistances = 0
  return [SumMovements, SumDistances]

In [17]:
def UnitVector(vector):
    return vector / np.linalg.norm(vector)

def AngleBetween(v1, v2):
    v1_u = UnitVector(v1)
    v2_u = UnitVector(v2)
    return np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))

def CalculateAngles(AnnotData, Robustness, Frequency, ComputerStartingFrame=0, ComputerEndingFrame=-1):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if element.frame>=ComputerStartingFrame and (ComputerEndingFrame==-1 or element.frame<=ComputerEndingFrame):
          if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
            Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])
            if not math.isnan(Angle):
              CurrentAngles += Angle
            pprevx = prevx
            pprevy = prevy
            prevx = element.posx
            prevy = element.posy
            NumElements += 1
          counter+=1
      CellAngles.append(CurrentAngles)

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  
  if NumElements!=0:
    SumAngles = sum(CellAngles)/NumElements
  else:
    SumAngles = 0

  return [SumAngles]

def CalculateNormAngles(AnnotData, Robustness, Frequency, ComputerStartingFrame=0, ComputerEndingFrame=-1):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if element.frame>=ComputerStartingFrame and (ComputerEndingFrame==-1 or element.frame<=ComputerEndingFrame):
          if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
            #Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*(np.sqrt(np.power(pprevx-prevx,2)+np.power(pprevy-prevy,2))+np.sqrt(np.power(prevx-element.posx,2)+np.power(prevy-element.posy,2)))
            Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*np.sqrt(np.power(pprevx-element.posx,2)+np.power(pprevy-element.posy,2))
            if not math.isnan(Angle):
              CurrentAngles += Angle
            pprevx = prevx
            pprevy = prevy
            prevx = element.posx
            prevy = element.posy
            NumElements += 1
          counter+=1
      CellAngles.append(CurrentAngles)

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  if NumElements!=0:
    SumAngles = sum(CellAngles)/NumElements
  else:
    SumAngles = 0

  return [SumAngles]

In [18]:
def ReadData(CellType, NameModifier, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]
      

In [19]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos/AllControls/')
AllCellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  AllCellTypes.append(splitted[0])
AllCellTypes.sort()
for CellType in AllCellTypes:
  print(CellType)

BIBF06_22
BIBF07_22
BIBF07_23
BIBF_01_1
BIBF_01_3
BIBF_01_7
BIBF_02_13
BIBF_02_20
BIBF_03_22
BIBF_03_24
BIBF_04_13
BIBF_04_19
BIBF_04_21
BRAF01_13
BRAF01_14
BRAF01_30
BRAF01_5
BRAF01_6
BRAF02_17
BRAF02_31
BRAF02_33
BRAF02_8
BRAF03_13
BRAF03_28
BRAF03_35
BRAF04_17
BRAF04_2
BRAF04_22
BRAF04_26
BRAF04_31
BRAF04_33
BRAF04_7
BRAF05_10
BRAF05_11
BRAF05_12
BRAF05_4
BRAF05_5
BRAF05_7
BRAF05_8
BRAF06_1
BRAF06_2
BRAF06_3
BRAF06_31
BRAF08_15
BRAF08_36
BRAF08_9
BRAF09_12
BRAF09_13
BRAF09_14
BRAF09_35
BRAF09_36
BRAF10_15
BRAF10_35
BRAF11_10
BRAF11_13
BRAF11_14
BRAF11_35
BRAF12_13
BRAF12_14
BRAF12_34
BRAF13_11
BRAF13_15
FAKinh01_12
FAKinh01_14
FAKinh01_4
FAKinh171010_1
FAKinh171010_16
FAKinh171010_2
FAKinh171010_6
FAKinh171010_8
FAKinh171010_9
MM05_19
MM05_20
MM05_22
MM05_24
T46_T47_drug01_20
T46_T47_drug01_21
T46_T47_drug01_4
T46_T47_drug01_5
T46_T47_drug02_20
T46_T47_drug02_5
T46_T47_siMVP_01_14
aktivin01_2
aktivin01_22
aktivin01_3
aktivin02_2
aktivin02_22
aktivin02_23
cldn4_02_19
cldn4_02_20
cldn

In [20]:
def DefineStartingAndEndingFrameOnComputerData(CellType, ComputerDataFolder):
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 
  ComputerAnnotList = ComputerAnnotFile.readlines()

  StartingFrame = -1
  EndingFrame = 0

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    if splitted[0].isdigit():
      CurrentFrame = int(splitted[0].strip())
      if CurrentFrame<StartingFrame or StartingFrame == -1:
        StartingFrame = CurrentFrame
      if CurrentFrame>EndingFrame:
        EndingFrame = CurrentFrame

  return [StartingFrame,EndingFrame]

In [21]:
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/02 Human Annotations/AllControls/"
ComputerDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/03 Estimated Paths/AllControls/"
ValidityFolder= "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Valid cell selector/outputs/"
OutCSVPath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Codes for calculations/AggregatingCalculations/outputs/AggregatingCalculations.csv"

ValidityFileName = "ValidCellsAllControlsInHumanRange.txt"

NameModifier= "_mimic_human"

OnlyValidCells = True
OnlyInComputerAnnotRange = True

In [37]:
#MAIN CODE

with open(OutCSVPath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(["","ScaleRation(H/C)","Correlation","NormCorrelation","LinearRegressionCoefficient(srt(R^2))","LinearRegressionSlope","LinearRegressionInterception"])

  AllHumanSumMovements=[]
  AllHumanSumDistances=[]
  AllHumanSumAngles=[]
  AllComputerSumMovements=[]
  AllComputerSumDistances=[]
  AllComputerSumAngles=[]
  AllComputerSumAnglesFreq=[]
  
  CellTypes = AllCellTypes
  if OnlyValidCells:

    ValidityFile = open(ValidityFolder+ValidityFileName,"r")
    ValidityList = ValidityFile.readlines()

    ValidCellTypes = []
    for VCellType in ValidityList:
      VSCellType = VCellType.strip()
      if VSCellType in CellTypes:
        ValidCellTypes.append(VSCellType)
    CellTypes = ValidCellTypes

  CalculationsDoneNum = 0
  for CellType in CellTypes:
    #Reading both files
    [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,NameModifier,HumanDataFolder,ComputerDataFolder)

    HumanAnnotFreq = GetFreq(HumanAnnotData)
    [ComputerStartingFrame, ComputerEndingFrame] = DefineStartingAndEndingFrameOnComputerData(CellType,ComputerDataFolder)

    #Calculating the movements for both data
    if OnlyInComputerAnnotRange:
      [HumanSumMovements, HumanSumDistances] = CalculateMovements(HumanAnnotData,0,1,ComputerStartingFrame=ComputerStartingFrame,ComputerEndingFrame=ComputerEndingFrame)
      [HumanSumAngles] = CalculateNormAngles(HumanAnnotData,0,1,ComputerStartingFrame=ComputerStartingFrame,ComputerEndingFrame=ComputerEndingFrame)
    else:
      [HumanSumMovements, HumanSumDistances] = CalculateMovements(HumanAnnotData,0,1)
      [HumanSumAngles] = CalculateNormAngles(HumanAnnotData,0,1)

    [ComputerSumMovements, ComputerSumDistances] = CalculateMovements(ComputerAnnotData,0,1)
    [ComputerSumMovementsFreq, ComputerSumDistancesFreq] = CalculateMovements(ComputerAnnotData,0,HumanAnnotFreq)
    [ComputerSumAngles] = CalculateNormAngles(ComputerAnnotData,0,1)
    [ComputerSumAnglesFreq] = CalculateNormAngles(ComputerAnnotData,0,HumanAnnotFreq)

    if HumanSumMovements!=0 and HumanSumAngles!=0:
      print(CellType+"\t"+str(CalculationsDoneNum+1)+"/"+str(len(CellTypes)))
      AllHumanSumMovements.append(HumanSumMovements)
      AllHumanSumDistances.append(HumanSumDistances)
      AllHumanSumAngles.append(HumanSumAngles)
      AllComputerSumMovements.append(ComputerSumMovements)
      AllComputerSumDistances.append(ComputerSumDistances)
      AllComputerSumAngles.append(ComputerSumAngles)
      AllComputerSumAnglesFreq.append(ComputerSumAnglesFreq)

    CalculationsDoneNum +=1

  HM = np.array(AllHumanSumMovements)
  HD = np.array(AllHumanSumDistances)
  HA = np.array(AllHumanSumAngles)
  CM = np.array(AllComputerSumMovements)
  CD = np.array(AllComputerSumDistances)
  CA = np.array(AllComputerSumAngles)
  CAF = np.array(AllComputerSumAnglesFreq)

  nHM = HM/np.sum(HM)
  nHD = HD/np.sum(HD)
  nHA = HA/np.sum(HA)
  nCM = CM/np.sum(CM)
  nCD = CD/np.sum(CD)
  nCA = CA/np.sum(CA)
  nCAF = CAF/np.sum(CAF)

  model = LinearRegression().fit(HM.reshape((-1, 1)),CM)
  CSVwriter.writerow(["HM-CM",sum(HM)/sum(CM),np.corrcoef(HM,CM)[0,1],np.corrcoef(nHM,nCM)[0,1], np.sqrt(model.score(HM.reshape((-1, 1)),CM)),model.coef_[0],model.intercept_])
  model = LinearRegression().fit(HD.reshape((-1, 1)),CD)
  CSVwriter.writerow(["HD-CD",sum(HD)/sum(CD),np.corrcoef(HD,CD)[0,1],np.corrcoef(nHD,nCD)[0,1], np.sqrt(model.score(HD.reshape((-1, 1)),CD)),model.coef_[0],model.intercept_])
  model = LinearRegression().fit(HA.reshape((-1, 1)),CA)
  CSVwriter.writerow(["HA-CA",sum(HA)/sum(CA),np.corrcoef(HA,CA)[0,1],np.corrcoef(nHA,nCA)[0,1], np.sqrt(model.score(HA.reshape((-1, 1)),CA)),model.coef_[0],model.intercept_])
  model = LinearRegression().fit(HA.reshape((-1, 1)),CAF)
  CSVwriter.writerow(["HA-CAF",sum(HA)/sum(CAF),np.corrcoef(HA,CAF)[0,1],np.corrcoef(nHA,nCAF)[0,1], np.sqrt(model.score(HA.reshape((-1, 1)),CAF)),model.coef_[0],model.intercept_])
  model = LinearRegression().fit((HM*HM).reshape((-1, 1)),(CM*CM))
  CSVwriter.writerow(["HM*HD-CM*CD",sum(HM*HM)/sum(CM*CM),np.corrcoef(HM*HD,CM*CD)[0,1],np.corrcoef(nHM*nHD,nCM*nCD)[0,1], np.sqrt(model.score((HM*HM).reshape((-1, 1)),CM*CM)),model.coef_[0],model.intercept_])

print("Run successfully finished")

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: RuntimeWarning: invalid value encountered in true_divide
  


BIBF06_22	1/342
BIBF07_22	2/342
BIBF07_23	3/342
BIBF_01_1	4/342
BIBF_01_3	5/342
BIBF_01_7	6/342
BIBF_03_22	8/342
BIBF_04_13	10/342
BRAF02_31	14/342
BRAF02_33	15/342
BRAF04_17	17/342
BRAF04_31	19/342
BRAF04_33	20/342
BRAF05_10	21/342
BRAF05_12	23/342
BRAF05_7	24/342
BRAF06_1	25/342
BRAF06_2	26/342
BRAF06_31	27/342
BRAF08_15	28/342
BRAF08_36	29/342
BRAF08_9	30/342
BRAF09_36	32/342
BRAF12_13	33/342
BRAF12_14	34/342
BRAF12_34	35/342
BRAF13_11	36/342
BRAF13_15	37/342
FAKinh01_12	38/342
FAKinh01_14	39/342
FAKinh01_4	40/342
FAKinh171010_1	41/342
FAKinh171010_16	42/342
FAKinh171010_2	43/342
FAKinh171010_6	44/342
FAKinh171010_8	45/342
FAKinh171010_9	46/342
MM05_19	47/342
MM05_20	48/342
MM05_22	49/342
MM05_24	50/342
T46_T47_drug01_20	51/342
T46_T47_drug01_21	52/342
T46_T47_drug01_4	53/342
T46_T47_drug01_5	54/342
T46_T47_drug02_20	55/342
T46_T47_drug02_5	56/342
T46_T47_siMVP_01_14	57/342
aktivin01_2	58/342
aktivin01_22	59/342
aktivin01_3	60/342
aktivin02_2	61/342
aktivin02_22	62/342
aktivin02_23	